In [287]:
import re
import pandas as pd
from collections import Counter, defaultdict
from nltk.tokenize import sent_tokenize, word_tokenize

In [245]:
with open('./data/Lexis Cases txt/P1.txt') as file:
    doc_count = 0
    conclusion_count = 0
    lines = file.readlines()
#     doc_info = dict()
    case_no = []
    registries = []
    paras = []
    curr_case = ''
    for line in lines:
        match_case = re.search(r'\[[0-9]{4}\] [[A-Z|\.]+ No\. [0-9]+', line)
        match_reg = re.match(r'Registry: ?([A-Za-z|\s]+)', line)
        match_paras = re.match(r'\(([0-9]+) paras\.?\)', line)
        if match_reg:
            registries.append(match_reg.group(1).strip())
        if match_case:
            case_no.append(match_case.group(0))
        if match_paras:
            paras.append(match_paras.group(1))
        if line == 'End of Document\n':
            doc_count+=1
            print('++++++++++')
        if re.match('conclusions?', line, re.IGNORECASE) and len(line.split()) < 10:
            print(line)
            
            
            

Conclusion

++++++++++
Conclusion re Future Care

CONCLUSION - DAMAGE AWARD

Conclusion re Future Care

CONCLUSION - DAMAGE AWARD

++++++++++
Conclusion

Conclusion

++++++++++
Conclusion on Contributory Negligence

CONCLUSION ON MS. HOWELL'S ONGOING DIFFICULTIES

CONCLUSION

Conclusion

Conclusion

Conclusion

Conclusion

Conclusion on Contributory Negligence

Conclusion on Ms. Howell's Ongoing Difficulties

Conclusion

Conclusion

Conclusion

Conclusion

Conclusion

++++++++++
++++++++++
++++++++++
++++++++++
Conclusion

++++++++++
++++++++++
CONCLUSIONS ON LIABILITY

Conclusion re Foreseeable Risks of Harm

CONCLUSION

CONCLUSIONS ON LIABILITY

Conclusion on Length of Time Patient was Unmonitored

Conclusion re Foreseeable Risks of Harm

CONCLUSION

++++++++++
++++++++++
++++++++++
Conclusion

++++++++++
++++++++++
++++++++++
Conclusion

++++++++++
++++++++++
++++++++++
Conclusion regarding Shannon Kemp's November 2006 admission to VGH

Conclusion regarding the Plaintiff's claims as

In [319]:
def parse_file(path):
    '''given file path, extract relevant info for each document in file 
    Return list of dictionary of document features per document '''
    with open(path) as file:
        docs = file.read().split('End of Document\n')[:-1]
    
    docs_feats = []
    for i in range(len(docs)):

        doc_dict = dict()
        case_no = re.search(r'\/P([0-9]+)', path).group(1)
        doc = docs[i]
        
        lines = doc.split('\n')
        if not 'British Columbia Judgments' in lines[1]:
            continue
        
        
        case_name = lines[0]
        judge_name = lines[4]
        registry = re.search(r'Registry:? ?([A-Za-z|\s|0-9|\.]+)', doc)
        no_paras = re.search(r'\(([0-9|,]+) paras?\.?\)', doc)
        doc_dict['case number'] = '%s of %s'%(i+1+((int(case_no)-1)*50), case_no)
        doc_dict['case name'] = case_name
        doc_dict['judge_name'] = judge_name
        if registry:
            doc_dict['registry'] = registry.group(1).strip()
        else:
            doc_dict['registry'] = None
            
        if no_paras:
            doc_dict['decision length'] = no_paras.group(1)
        else:
            doc_dict['decision length'] = None
        doc_dict['contributory negligence raised'] = False
        
        damages_headers = set()
        conclusions = set()
        all_headers = set()
        for line in lines:
            
            if re.match('contributory negligence', line, re.IGNORECASE): #this isnt working...
                doc_dict['contributory negligence raised'] = True
                
            concl_match = re.match('conclusions?', line, re.IGNORECASE)
            if concl_match and len(line.split()) < 10:
                conclusions.add(line)
            damages = re.match('damages', line, re.IGNORECASE)
            if damages and len(line.split()) < 10:
                damages_headers.add(line)
        doc_dict['damages_headers'] = damages_headers
        doc_dict['conclusion_headers'] = conclusions
        
        if damages_headers != set():
            for damages in damages_headers:
                text = doc.split(damages)[-1]
                damages_mentioned = re.findall(r'\$[0-9|,]+', text)
                if len(damages_mentioned) > 0:
                    doc_dict['$$ under header <%s>'%damages] = damages_mentioned
                    
        if conclusions != set():
            for conc in conclusions:
                text = doc.split(conc)[-1]
                damages_mentioned = re.findall(r'\$[0-9|,]+', text)
                if len(damages_mentioned) > 0:
                    doc_dict['$$ under header <%s>'%conc] = damages_mentioned            
        docs_feats.append(doc_dict)
#     df = pd.DataFrame(docs_feats)
    return docs_feats

In [320]:
docs_feats = parse_file('./data/Lexis Cases txt/P2.txt')
docs_feats

[{'case number': '52 of 2',
  'case name': "Nelson v. Provincial Health Services Authority (c.o.b. British Columbia Women's Hospital and Health Centre), [2015] B.C.J. No. 2316",
  'judge_name': 'R. Johnston J.',
  'registry': 'Victoria',
  'decision length': '166',
  'contributory negligence raised': False,
  'damages_headers': {'Damages'},
  'conclusion_headers': set(),
  '$$ under header <Damages>': ['$17,415',
   '$100,000',
   '$775,000',
   '$275,000',
   '$4,500',
   '$17,415',
   '$1,171,915']},
 {'case number': '53 of 2',
  'case name': 'Ruchelski v. Moore, [2013] B.C.J. No. 561',
  'judge_name': 'P. Abrioux J.',
  'registry': 'Vernon',
  'decision length': '110',
  'contributory negligence raised': False,
  'damages_headers': set(),
  'conclusion_headers': set()},
 {'case number': '54 of 2',
  'case name': 'Steinebach (Litigation guardian of) v. Fraser Health Authority (c.o.b. Surrey Memorial Hospital), [2010] B.C.J. No. 1129',
  'judge_name': 'I.H. Pitfield J.',
  'registry':

In [83]:
seq = re.compile(r"conclusions?:?.*", re.MULTILINE|re.IGNORECASE)
for match in seq.finditer(docs[1]):
    print(match.group(0))

CONCLUSIONS
Conclusion re Future Care
CONCLUSION - DAMAGE AWARD
CONCLUSIONS
conclusions are these.
conclusion of the forceps attempt.
conclusion of the forceps attempt.
conclusion that it is more likely than not the conduct of the defendant was a cause in fact of the result. A mere possibility of such causation is not enough; and when the matter remains one of pure speculation or conjecture, or the probabilities are at best evenly balanced, it becomes the duty of the court to direct a verdict for the defendant.
conclusion in Cherry v. Borsman, as described above, may no longer apply. This enlarged position effectively subsumes Dr. Johnston's original position. However, because of the manner in which the case was presented and argued in the trial, with further written submissions after judgment was reserved, it seems most convenient and responsive to the weight and direction of counsels' submissions to address first the matter of informed consent and the fetus, and then the larger quest

### Trying to find patterns in damages awarded

Print all paragraphs with  dollar values in them 

In [379]:
no_paras = re.search(r'\(([0-9|,]+) paras?\.?\)', docs[0]).group(1)
pattern = r'[\W|\w]?(?=\n[0-9]{1,%s}[\xa0|\s| ]{2})'%len(no_paras)

paras_split = re.split(pattern, docs[0])
paras_split[-1]

'\n115\xa0\xa0In the result, I find liability is apportioned 50% to each party.\nS.F. KELLEHER J.\n'

In [561]:
def paragraph_tokenize(file_name):
    '''Print document by paragraph number. If quantity mentioned, print values.
    Return list of lists of numbered paragraphs per document'''

    with open(file_name) as file:
        docs = file.read().split('End of Document\n')[:-1]
    
    docs_split = []
#     for doc in docs:
    for doc in docs:
        print('@@NEW DOC@@')
        lines = doc.split('\n')
        if not 'British Columbia Judgments' in lines[1]:
            continue
        no_paras = re.search(r'\(([0-9|,]+) paras?\.?\)', doc).group(1)
        print('NUM OF PARAS: %s'%no_paras)
#         if no_paras:
#             no_paras = no_paras.group(1)
        pattern = r'[\W|\w]?(?=\n[0-9]{1,%s}[\xa0|\s| ]{2})'%len(no_paras)

        paras_split = re.split(pattern, doc)
        paras = []
        for para in paras_split:
#             prev_para_no = 0
            
            para_start = re.match(r'^\n([0-9]{1,%s})[\xa0]{2}'%len(no_paras), para)
            if para_start:
#                 if int(para_start.group(1)) == int(prev_para_no)+1 or prev_para_no == 0:
                print(para)
                paras.append(para)
                quantity_mentioned = re.findall(r'(?:\$?(?<!\n)(?:[0-9]{1,3},?\.?[0-9]{1,3}?)%?(?![\xa0]{2}|:)+)', para)
                if len(quantity_mentioned) > 0:
                    print('QUANTITY MENTIONED')
                    print(quantity_mentioned)
                if para in paras_split[-5:]:
                    print('ONE OF LAST 5 PARAGRAPHS - DAMAGES HERE???')
                print('======')
#         docs_split.append(paras)
    return docs_split

In [562]:
path = './data/Lexis Cases txt/P1.txt'
doc_split = paragraph_tokenize(path)

@@NEW DOC@@
NUM OF PARAS: 115

1   This is a summary trial. The plaintiff's claim arises out of a pedestrian/motor vehicle accident. Mansurali Mawani was struck by a vehicle driven by the defendant Peter Pitcairn. The claim against British Columbia Hydro and Power Authority has been discontinued

2  The defendant Pitcairn applies for an order pursuant to Rule 9-7(15) of the Supreme Court Civil Rules, B.C. Reg. 168/2009, that the plaintiff's claim against the defendant be dismissed with costs. The plaintiff seeks a decision that the defendant is 100% liable for the accident
QUANTITY MENTIONED
['15', '168', '2009', '100%']

3  Depending on the outcome of these issues, consideration may have to be given to contributory negligence

4  The accident occurred on February 1, 2007, at approximately 6:40 a.m. It happened on Steveston Highway in Richmond, between Bamberton Drive and McKenzie Road
QUANTITY MENTIONED
['2007', '40']

5  The defendant was driving a 2005 Ford F350 pickup truck. He and

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [541]:
doc_feats = defaultdict(lambda: defaultdict(dict))

for i in range(len(doc_split)):
    doc = doc_split[i]
    for j in range(len(doc)):
        para = doc[j]
        quantity_mentioned = re.findall(r'\$?(?<!\n)(?:[^\D\n][0-9]{1,3},?\.?[0-9]{1,3}?)(?![\xa0]{2})+%?', para)
        if len(quantity_mentioned) > 0:
            doc_feats['document number %s'%i]['paragraph %s'%j]['quantities_found']  = True
            for quantities in quantity_mentioned:
            
                
        else:
            doc_feats['document number %s'%i]['paragraph %s'%j]['quantities_found']  = False
        doc_feats['document number %s'%i]['paragraph %s'%j]['quantities'] = quantity_mentioned

In [542]:
doc_feats

defaultdict(<function __main__.<lambda>()>,
            {'document number 0': defaultdict(dict,
                         {'paragraph 0': {'quantities_found': False,
                           'quantities': []},
                          'paragraph 1': {'quantities_found': True,
                           'quantities': ['168', '2009', '100%']},
                          'paragraph 2': {'quantities_found': False,
                           'quantities': []},
                          'paragraph 3': {'quantities_found': True,
                           'quantities': ['2007']},
                          'paragraph 4': {'quantities_found': True,
                           'quantities': ['2005', '350']},
                          'paragraph 5': {'quantities_found': False,
                           'quantities': []},
                          'paragraph 6': {'quantities_found': True,
                           'quantities': ['2008']},
                          'paragraph 7': {'quantities_fou